In [ ]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns
from matplotlib.cm import get_cmap, ListedColormap
import pylab as pl
from scipy.optimize import curve_fit, fsolve
from mpl_toolkits.axes_grid1.inset_locator import inset_axes
from scipy.stats import kruskal, shapiro, norm
from pandas.api.types import CategoricalDtype
import scikit_posthocs as sp
from pygam import s, GammaGAM
from matplotlib.ticker import LinearLocator
from scipy.stats import mannwhitneyu


In [ ]:
def rm_sediment_noise(df, datetime_to_rm): 
    """Removal of noise artifacts due to sediment disturbance unrelated to sea state or anthropogenic activity.
df: pandas DataFrame containing at least a 'datetime' column with datetime objects.
datetime_to_rm: list of datetime strings (e.g. ['2021-01-15 14:00:00', '2021-01-16 09:00:00']) representing the hours to be removed from the dataframe.
"""
    df_clean = df.copy()
    datetime_to_rm = pd.to_datetime(datetime_to_rm).floor('h')
    df_clean['hour'] = df_clean['datetime'].dt.floor('h')
    df_clean = df_clean[~df_clean['hour'].isin(datetime_to_rm)]
    df_clean = df_clean.drop(columns='hour')
    return df_clean

In [ ]:
def plot_with_inset_mean(df, db_value, output_path):
    """Function to generate Figure 5 to choose the cutting point between low and high sea state.
df : pandas DataFrame containing at least 'beaufort' and db_value columns.
db_value : name of the column containing the dB re 1µPa²
output_path : path to save the figure."""
    fig, ax = plt.subplots(figsize=(10, 5), constrained_layout=True)

    counts, bins, _ = ax.hist(df[db_value], bins=60, density=True, alpha=0.4,
                               color='gray', edgecolor='black')
    x = np.linspace(min(bins), max(bins), 500)

    beaufort_values = sorted(df["beaufort"].dropna().unique())
    n_colors = len(beaufort_values)
    cmap = get_cmap("tab20")
    colors = [cmap(i / n_colors) for i in range(n_colors)]

    bf_means = []

    for bf, color in zip(beaufort_values, colors):
        subset = df[df["beaufort"] == bf][db_value].dropna()
        mu, sigma = norm.fit(subset)
        y = norm.pdf(x, mu, sigma)
        ax.plot(x, y, color=color, lw=2, label=f"Beaufort {bf}")
        bf_means.append((bf, mu)) 

    ax.set_xlabel("dB re 1µPa²/Hz level for the 10–400 Hz frequency band", fontsize=12)
    ax.set_ylabel("Density", fontsize=12)
    ax.set_title("")
    ax.legend(loc='upper left', bbox_to_anchor=(0.01, 1.01))
    ax.tick_params(labelsize=12)

    inset_ax = inset_axes(ax, width="30%", height="60%", loc='upper right', borderpad=1)

    bf_vals, db_means = zip(*bf_means)
    inset_ax.plot(bf_vals, db_means, 'ko--')
    inset_ax.set_title("")
    inset_ax.set_xlabel("Beaufort state", fontsize=12)
    inset_ax.set_ylabel("Mean dB re 1µPa²/Hz", fontsize=12)
    inset_ax.tick_params(labelsize=12)
    inset_ax.grid(True)

    plt.savefig(output_path, dpi=600, bbox_inches='tight')
    plt.show()

In [ ]:
def cutting_anthro(df, db_band, output_path):
    """Function to generate Figure 6 to define the cutting threshold between low and high anthropophony.
df : pandas DataFrame containing at least db value for the 10-400 Hz band
db_band : name of the column containing the dB re 1µPa² for the choosen selected band
output_path : path to save the figure."""
    df = df.copy()
    df_low = df[df['beaufort'] < 6]
    raw_values = df_low[db_band].values

    def double_gaussian(x, A1, mu1, sigma1, A2, mu2, sigma2):
        return (A1 * norm.pdf(x, mu1, sigma1) + 
                A2 * norm.pdf(x, mu2, sigma2))
    
    def find_intersection(A1, mu1, sigma1, A2, mu2, sigma2):
        def diff(x):
            return (A1 * norm.pdf(x, mu1, sigma1) -
                    A2 * norm.pdf(x, mu2, sigma2))
        x0 = (mu1 + mu2) / 2 
        x_intersection = fsolve(diff, x0)
        return x_intersection[0]

    counts, bin_edges = np.histogram(raw_values, bins=100, density=False)
    bin_centers = (bin_edges[:-1] + bin_edges[1:]) / 2

    mu1_guess = np.percentile(raw_values, 25)
    mu2_guess = np.percentile(raw_values, 75)
    init_params = [0.05, mu1_guess, 3, 0.04, mu2_guess, 2]    
    popt, pcov = curve_fit(double_gaussian, bin_centers, counts, p0=init_params)
    intersection = find_intersection(*popt)
    print(f"Intersection at x = {intersection:.2f} dB")

    x = np.linspace(np.min(raw_values), np.max(raw_values), 500)

    plt.figure(figsize=(10, 6))
    full_values = df[db_band].dropna()
    full_counts, _ = np.histogram(full_values, bins=bin_edges, density=False)
    plt.bar(bin_centers, full_counts, width=bin_edges[1]-bin_edges[0],
            alpha=0.2, color='gray', label='Full data (all Beaufort)', zorder=0)

    plt.bar(bin_centers, counts, width=bin_edges[1]-bin_edges[0], alpha=0.5, color='skyblue', label='Beaufort > 5')
    plt.plot(x, popt[0] * norm.pdf(x, popt[1], popt[2]), 'r-', label='Distribution 1')
    plt.plot(x, popt[3] * norm.pdf(x, popt[4], popt[5]), 'g-', label='Distribution 2')
    plt.plot(x, double_gaussian(x, *popt), 'k-', label='Global distribution')

    y_intersection = double_gaussian(intersection, *popt)
    plt.plot([intersection, intersection], [0, y_intersection], 'k--', linewidth=1.5, label='Intersection')
    plt.xlabel("dB re 1µPa²/Hz level in the 10–400 Hz frequency band", fontsize=12)
    plt.ylabel("Counts", fontsize=12)
    xticks = np.arange(int(min(bin_edges)), int(max(bin_edges)) + 1, 2)
    plt.xticks(xticks)
    plt.xlim(67, 89)
    plt.tick_params(labelsize=12)
    plt.legend(fontsize=12)
    plt.title("")
    plt.savefig(output_path, dpi=600, bbox_inches='tight')
    plt.show()

    return intersection

In [ ]:
def compute_detection_rate(df, group_term, db_column, file_list):
    """Function to compute detection rates of cetaceans vocalization over specified time frames.
df: pandas DataFrame containing at least 'datetime', vocalization count for each species by recording, duration of the recording, and the mean dB value for a specified frequency band.
group_term: string representing the time frame to group by (e.g., day, 24 hour of the clock, every hour for each day, light state)
file_list: list of all the file."""
    cet_columns = ['cet_count_bosse', 'cet_count_orque', 'cet_count_rorqual']
    df = df.copy()
    df['day'] = df['datetime'].dt.floor('D')
    df['hour']=df['datetime'].dt.hour
    df['date_hour'] = df['datetime'].dt.floor('h')
    prov = pd.DataFrame(file_list[group_term].drop_duplicates())
    DR = df.groupby(group_term).agg({**{col: 'sum' for col in cet_columns}, 'speed_m/s' : ['mean'], 'duration(min)' : ['sum'], db_column: ['mean', lambda x: x.quantile(0.25), lambda x: x.quantile(0.75)]}).reset_index()
    DR.columns = ['_'.join(col).strip('_') if isinstance(col, tuple) else col for col in DR.columns]
    DR.rename(columns={f'{db_column}_mean': f'db_mean', f'{db_column}_<lambda_0>': f'db_q1', f'{db_column}_<lambda_1>': f'db_q3', **{f'{col}_sum': col for col in cet_columns}, 'duration(min)_sum' : 'duration_record'}, inplace=True)
    for col in cet_columns:
        DR[f'detec_rate_{col}'] = DR[col] / DR['duration_record'] 
    DR=pd.merge(DR, prov, on = group_term, how = 'right')
    return DR

In [ ]:
def compute_presence_rate(df, group_term, db_column, file_list):
    """Function to compute presence rate over specified time frames.
df: pandas DataFrame containing at least 'datetime', vocalization count for each species by recording, and the mean dB value for a specified frequency band.
group_term: string representing the time frame to group by (e.g., day, 24 hour of the clock, every hour for each day, light state)
file_list: list of all the file.
"""
    cet_columns = ['cet_count_bosse', 'cet_count_orque', 'cet_count_rorqual']
    df = df.copy()
    df['day'] = df['datetime'].dt.floor('D')
    df['hour']=df['datetime'].dt.hour
    df['date_hour'] = df['datetime'].dt.floor('h')
    PR = df.groupby(group_term).agg({**{col: lambda x: (x > 0).sum() for col in cet_columns}, db_column:['mean']}).reset_index()
    PR.columns = ['_'.join(col).strip('_') if isinstance(col, tuple) else col for col in PR.columns]
    PR.rename(columns={f'{db_column}_mean': f'db_mean', **{f'{col}_<lambda>': col for col in cet_columns}}, inplace=True)
    record_counts = df.groupby(group_term).size().reset_index(name='nb_record')
    PR = pd.merge(PR, record_counts, on=group_term, how='right')
    for col in cet_columns:
        PR[f'presence_rate_{col}'] = (PR[col] / PR['nb_record'])*100
    prov = pd.DataFrame(file_list[group_term].drop_duplicates())
    PR = pd.merge(PR, prov, on=group_term, how='right')
    return PR

In [ ]:
def calendar_noise_plot(df, dsp_band, output_path, start_date=None, end_date=None):
    """Function to generate calendar plot of noise levels (Figure 7).
df : pandas DataFrame containing at least 'datetime' and dsp_band columns.
dsp_band : name of the column containing the dB re 1µPa² for the choosen selected band
output_path : path to save the figure.
start_date : optional string representing the start date to filter the data (e.g., '2021-01-01')
end_date : optional string representing the end date to filter the data (e.g., '2021-12-31')
""" 

    if start_date:
        df = df[df['datetime'] >= pd.to_datetime(start_date)]
    if end_date:
        df = df[df['datetime'] <= pd.to_datetime(end_date)]
        
    fig, ((ax, ax_hour), (ax_day, ax_legend)) = plt.subplots(2, 2, figsize=(15, 7), gridspec_kw={'width_ratios': [6, 1], 'height_ratios': [4, 1], 'left': 0.1, 
                                                                                                 'right': 0.9, 'bottom': 0.1, 'top': 0.9, 'wspace': 0.15, 'hspace': 0.30})

    cax = ax.imshow(df.groupby([df['datetime'].dt.strftime('%Y-%m-%d'), df['datetime'].dt.strftime('%H:00')])[dsp_band].mean().unstack(level=0), cmap='jet', aspect='auto')

    cbar = fig.colorbar(cax, cax=ax_legend, label='dB re 1 µPa²/Hz', orientation='horizontal')
    cbar.ax.xaxis.label.set_size(12) 
    vmin, vmax = cax.get_clim()

    grouped = df.groupby(df['datetime'].dt.strftime('%H:00'))[dsp_band]
    mean_per_hour = grouped.mean()
    q1_per_hour = grouped.quantile(0.25)
    q3_per_hour = grouped.quantile(0.75)

    ax_hour.plot(df.groupby([df['datetime'].dt.strftime('%H:00')])[dsp_band].mean(), 
                 df.groupby([df['datetime'].dt.strftime('%H:00')])[dsp_band].mean().index, color='#1f77b4')
    ax_hour.fill_betweenx(mean_per_hour.index, q1_per_hour, q3_per_hour, alpha=0.1, color='#1f77b4')


    grouped_day = df.groupby(df['datetime'].dt.strftime('%Y-%m-%d'))[dsp_band]
    mean_per_day = grouped_day.mean()
    q1_per_day = grouped_day.quantile(0.25)
    q3_per_day = grouped_day.quantile(0.75)

    ax_day.plot(mean_per_day.index, mean_per_day.values, color='#1f77b4')
    ax_day.fill_between(mean_per_day.index, q1_per_day, q3_per_day,  alpha=0.1, color='#1f77b4')

    ax_legend.set_xticks(np.linspace(vmin, vmax, 3))
    ax_legend.set_xticklabels([f"{x:.1f}" for x in np.linspace(vmin, vmax, 3)], fontsize=12)
    ax_day.set_xticks(np.arange(0, len(pd.to_datetime(df.groupby([df['datetime'].dt.strftime('%Y-%m-%d')])[dsp_band].mean().index.tolist()).strftime('%d-%m')), 2))
    ax_day.set_xticklabels(pd.to_datetime(df.groupby([df['datetime'].dt.strftime('%Y-%m-%d')])[dsp_band].mean().index).strftime('%d-%m')[::2], fontsize=12)  
    ax.set_xticks([])
    ax_day.tick_params(axis='x', rotation=90)
    ax_day.tick_params(axis='y', labelsize=12)
    ax_hour.tick_params(axis='y', labelsize=12)
    ax.tick_params(axis='y', labelsize=12)

    ax_day.set_ylabel('dB re 1 µPa²/Hz', fontsize=12)
    ax.set_ylabel('Hour (UTC+1)', fontsize=12)
    ax_day.set_xlabel('Date', fontsize=12)
    ax_hour.set_xlabel('dB re 1 µPa²/Hz', fontsize=12)


    types_la = ['top', 'bottom', 'left', 'right']    
    for t in types_la:
        ax_day.spines[t].set_visible(False)
        ax_hour.spines[t].set_visible(False)
    
    ax_hour.invert_yaxis()
    ax_hour.grid(alpha=.5)
    ax_day.grid(alpha=.5)

    ax.set_position([0.025, 0.18, 0.5, 0.52])
    ax_hour.set_position([0.58, 0.157, 0.1, 0.57])
    ax_legend.set_position([0.59, 0.031, 0.08, 0.04])
    ax_day.set_position([0, 0.01, 0.55, 0.15])

    plt.tight_layout()
    plt.savefig(output_path, dpi=600, bbox_inches='tight')
    plt.show()


In [ ]:
def plot_calendar_daily(df, save_path, df_columns, cmap_list, rate, df_name="Dataset", showfig = False):
    """Function to generate calendar plot of daily detection or presence rates (Figure 9).
df : pandas DataFrame containing at least 'day' and detection/presence rate columns.
save_path : path to save the figure.
df_columns : list of column names to plot (e.g., detection rates for different species).
cmap_list : list of colormaps corresponding to each df_column.
rate : string representing the rate type (e.g., 'DR (voc/min)').
df_name : title of the figure.
"""
    df['month'] = df['day'].dt.month
    df['jour'] = df['day'].dt.day
    mois_ordonne = ['11', '12', '1'] 

    labels = ['Fin whale', 'Humpback whale', 'Orca'] 
    fig, axs = plt.subplots(3, 1, figsize=(8,6), gridspec_kw={'wspace':0.05, 'hspace':0.23})
    fig.suptitle(df_name, fontsize=14, y=0.93)

    for i, col in enumerate(df_columns):
        calendar_matrix = df.pivot(index='month', columns='jour', values=col)
        calendar_matrix.index = calendar_matrix.index.astype(str)
        calendar_matrix = calendar_matrix.loc[mois_ordonne]

        cax = axs[i].imshow(calendar_matrix.values, cmap=cmap_list[i],
                            aspect='auto', interpolation='nearest')

        # marquer les NaN
        nan_positions = calendar_matrix.isna().loc[mois_ordonne]
        for idx, month in enumerate(calendar_matrix.index):  
            for j, day in enumerate(calendar_matrix.columns):  
                if nan_positions.loc[month, day]: 
                    axs[i].plot(j, idx, 'k.', markersize=5)  

        cbar = plt.colorbar(cax, ax=axs[i], label=rate, pad=0.02, fraction=0.08, aspect=8)
        cbar.set_label(rate, fontsize=12)
        cbar.update_ticks()
        cbar.ax.tick_params(labelsize=12)
        axs[i].set_title(labels[i], fontsize=12) 
        axs[i].set_xticks(np.arange(0, 32, 2),
                          [str(i) for i in range(1, 32, 2)], fontsize=12) 
        axs[i].set_yticks(np.arange(len(sorted(df['month'].unique()))),
                          [str(i) for i in ['Nov', 'Dec', 'Jan']], fontsize=12) 
        if i == len(df_columns) - 1:   # seulement dernier subplot
            axs[i].set_xlabel("Day", fontsize=12)
        else:
            axs[i].set_xticklabels([])  # supprime les labels de ticks
            axs[i].set_xticks([]) 
    
    plt.savefig(save_path, dpi=600, bbox_inches='tight')
    if showfig:
        plt.show()
    plt.close()

In [ ]:
def line_plot(df, col, db_band, output_path, title=''):
    """Function to generate Figure 8 - Density plot of noise levels by light state.
df : pandas DataFrame containing at least 'light_state' and db_band columns.
db_band : name of the column containing the dB re 1µPa² for the choosen selected band
output_path : path to save the figure."""
    custom_order = ['dark', 'dawn', 'light', 'dusk']
    palette = {"light": "#F28B82", "dark": "#B0B0B0", "dusk": "#77DD77",  "dawn": "#AECBFA"}

    fig, ax = plt.subplots(figsize=(10, 6))
    for state in custom_order:
        subset = df[df['light_state'] == state]
        sns.kdeplot(data=subset, x=col, ax=ax, label=state, color=palette[state], linewidth=3)

    ax.set_title(title, fontsize=14)
    ax.set_xlabel('dB re 1µPa²/Hz level in 10-400 Hz', fontsize=12)
    ax.set_ylabel('Density', fontsize=12)
    ax.legend(title='light state', fontsize=12, title_fontsize='14')
    ax.tick_params(axis='both', labelsize=12)
    ax.set_xticks(np.arange(start=np.floor(df[col].min()), stop=np.ceil(df[col].max()) + 1, step=2))
    ax.set_xlim(df[col].min(), 90)
    plt.grid()
    plt.tight_layout()
    plt.savefig(output_path, dpi=600)
    plt.show()

In [ ]:
def light_state_plot(df, save_path, rate, colors, cet_columns, species_mapping, showfig = False):
    """Function to generate boxplot of detection/presence rates by light state with statistical annotations (Figure 10).
df : pandas DataFrame containing at least 'light_state' and detection/presence rate columns.
save_path : path to save the figure.
rate : string representing the rate type (e.g., 'DR (voc/min)').
colors : dictionary mapping light states to colors.
cet_columns : list of column names representing different cetacean species.
species_mapping : dictionary mapping cetacean column names to species names."""
    custom_order = ['dark', 'dawn', 'light', 'dusk']
    light_cat_type = CategoricalDtype(categories=custom_order, ordered=True)
    df['light_state'] = df['light_state'].astype(light_cat_type)
    df = df.melt(id_vars=['light_state'], 
                                value_vars=cet_columns, 
                                var_name='Species', value_name=rate)
    df['Species'] = df['Species'].map(species_mapping)

    plt.figure(figsize=(8, 6)) 
    ax = sns.boxplot(x="Species", y=rate, hue="light_state", data=df, palette = colors, showfliers=False, linewidth=0.8, showmeans=True, meanprops={"marker":"o","markerfacecolor":"white", "markeredgecolor":"black", "markersize":"3"})
    plt.ylabel(f'{rate}', fontsize=12)
    plt.xlabel('')
    plt.legend(title=False, loc='center right', fontsize=12, bbox_to_anchor =(1.0, 0.8))
    plt.xticks(fontsize=12)

    
    x_positions = {esp: i for i, esp in enumerate(df["Species"].unique())}
    light_states = df["light_state"].unique()
    state_positions = {state: i for i, state in enumerate(df['light_state'].cat.categories)}
    
    kruskal_results = {}
    posthoc_results_dict = {}
    normality_result = {}

    for species in df["Species"].unique():
        subset = df[df["Species"] == species]
        normality_result[species] = {}

        for state in light_states:
            data = subset[subset['light_state'] == state][rate].dropna()
            stat, p = shapiro(data)
            normality_result[species][state] = (stat, p)
            print(f"Shapiro-Wilk test for {species} in {state}: W={stat:.3f}, p={p:.4f}")

        data_groups = [subset[subset['light_state'] == state][rate].values for state in light_states]
    
        H_stat, p_value = kruskal(*data_groups)
        kruskal_results[species] = {'H_stat': H_stat, 'p_value': p_value}
        print(f"Kruskal-Wallis test for {species}: H={H_stat:.3f}, p={p_value:.4f}")
    
   
        posthoc_results = sp.posthoc_dunn(subset, val_col=rate, group_col='light_state', p_adjust='bonferroni')
        posthoc_results_dict[species] = posthoc_results
        print(f"Post-hoc test results for {species}:")
        print(posthoc_results)

        def add_significance(ax, posthoc_results, x_pos, y_start, y_gap=0.2):
            comparisons = {}  

            for i, state1 in enumerate(posthoc_results.index):
                for j, state2 in enumerate(posthoc_results.columns):
                    if i < j: 
                        p_val = posthoc_results.loc[state1, state2]
                        if p_val <= 0.001:
                            symbol = '***'
                        elif p_val <= 0.01:
                            symbol = '**'
                        elif p_val <= 0.05:
                            symbol = '*'
                        else:
                            continue  

                        x1 = x_pos + state_positions[state1] * 0.2 - 0.2  
                        x2 = x_pos + state_positions[state2] * 0.2 - 0.2
                        
                        key = (state1, state2)
                        y = comparisons.get(key, y_start) 
                        
                        ax.plot([x1, x1, x2, x2], [y, y+0.2, y+0.2, y], lw=1, c='black') 
                        ax.text((x1 + x2) / 2, y + 0.2, symbol, ha='center', va='bottom', color='black') 

                        comparisons[key] = y + y_gap  

    y_max = df[rate].quantile(0.98)  

    for species, posthoc_results in posthoc_results_dict.items():
        x_pos = x_positions[species]  
        add_significance(ax, posthoc_results, x_pos, y_max)

    plt.savefig(save_path, dpi=600, bbox_inches='tight')
    plt.show()


In [ ]:
def calendar_plot(df, columns, save_path, titles, colorbar_label, clim_dict, tick_entier=True, showfig=False):
    """Function to generate calendar plot of hourly detection/presence rates (Figure 11).
df : pandas DataFrame containing at least 'date_hour' format 'YYYY-MM-DD HH:00:00' and detection/presence rate columns.
columns : list of column names to plot (e.g., detection/presence rates for different species).
save_path : path to save the figure.
titles : list of titles for each subplot.
colorbar_label : label for the colorbar.
clim_dict : dictionary specifying color limits for each column (e.g., {'fin': (0, 5), 'humpback': (0, 10), 'orca': (0, 3)})
tick_entier : boolean indicating whether to use integer ticks on the colorbar.
"""
    fig, axs = plt.subplots(3, 1, figsize=(6, 8))
    for i, col in enumerate(columns):
        matrix_data = df.pivot_table(values=col, index=df['date_hour'].dt.hour, columns=df['date_hour'].dt.floor('D'))
        cmap = plt.cm.YlGnBu
        cmap = cmap(np.linspace(0, 1, 256))
        cmap[0] = [0.8, 0.8, 0.8, 1]
        cmap = ListedColormap(cmap)
        cmap.set_under('white')
        vmin, vmax = clim_dict.get(col, (None, None))
        cax = axs[i].imshow(matrix_data, aspect='auto', cmap=cmap, vmin=vmin, vmax=vmax)
        axs[i].set_title(titles[i], fontsize=14)
        dates = matrix_data.columns
        tick_positions = np.arange(0, len(dates), 5)

        axs[i].tick_params(axis='y', labelsize=12)        


        cbar = fig.colorbar(cax, ax=axs[i], pad =0.02, fraction=0.08, aspect=10)
        cbar.set_label(colorbar_label, fontsize=13)
        cbar.locator = LinearLocator(numticks=5)
        cbar.update_ticks()
        if tick_entier:
            cbar.ax.yaxis.set_major_formatter('{x:.0f}')
        else:
            cbar.ax.yaxis.set_major_formatter('{x:.2f}')
        cbar.ax.tick_params(labelsize=12)

        if i == len(columns) - 1: 
            if len(tick_positions) > 0:
                axs[i].set_xticks(tick_positions)
                axs[i].set_xticklabels([dates[i].strftime('%Y-%m-%d') for i in tick_positions], rotation=90, fontsize=13)
        else:
            axs[i].set_xticklabels([])  # supprime les labels de ticks
            axs[i].set_xticks([]) 

    plt.tight_layout()
    plt.legend()
    plt.savefig(save_path, bbox_inches='tight', dpi=600)
    if showfig:
        plt.show()
    plt.close()

In [ ]:
def plot_gam(df, cet_col, cet_name, cet_colors, date_col, ax=None, save_path=None, show=True, ylim=None):
    """Function to plot Generalized Additive Model (GAM) results for cetacean detection rates (Figure 12).
    df: pandas DataFrame containing at least date_col and cet_col columns.
    cet_col: string representing the column name for cetacean detection rate.
    cet_name: string representing the name of the cetacean species.
    cet_colors: string representing the color for the plot.
    date_col: string representing the column name for datetime objects.
    ax: matplotlib Axes object to plot on. If None, a new figure and axes will be created.
    save_path: string representing the path to save the figure. If None, the figure will not be saved.
    show: boolean indicating whether to display the plot.
    ylim: tuple representing the y-axis limits. If None, default limits will be used."""
    df = df.dropna(subset=[cet_col])
    df['hour'] = df[date_col].dt.hour
    X = df[['hour']].values
    y = df[cet_col].values
    epsilon = 1e-5 
    y = np.where(y == 0, epsilon, y)    
    
    gam = GammaGAM(s(0), max_iter=500).fit(X, y)

    XX = np.linspace(0, 23, 96).reshape(-1, 1)
    partial, confi = gam.partial_dependence(term=0, X=XX, width=0.95)

    if ax is None:
        fig, ax = plt.subplots(figsize=(10, 5))

    ax.plot(XX, partial, color=cet_colors, label=cet_name)
    ax.fill_between(XX.ravel(), confi[:, 0], confi[:, 1], color=cet_colors, alpha=0.1, label='')
    ax.set_xlabel('Hour of the day', fontsize=12)
    ax.set_ylabel('s(hour)', fontsize=12)
    ax.grid(True)
    
    ax.tick_params(axis='y', labelsize=12)
    ax.tick_params(axis='x', labelsize=12)
    if ylim is not None:
        ax.set_ylim(ylim)
    
    if show and ax is None:
        plt.tight_layout()
        plt.show()
    
    if save_path:
        plt.savefig(save_path, dpi=600, bbox_inches='tight')
    print(f'GAM model for {cet_name}:', gam.summary())

In [ ]:
def mann_whitney_comparaison(df_low, df_high, colonnes):
    """Function to perform Mann-Whitney U test between low and high conditions (here anthropophony) for specified columns.
    df_low : pandas DataFrame for low condition (e.g., low anthropophony).
    df_high : pandas DataFrame for high condition (e.g., high anthropophony).
    colonnes : list of column names to perform the test on."""
    for col in colonnes:
        low = df_low[col].dropna()
        low = low[low != 0]
        high = df_high[col].dropna()
        high = high[high != 0]
        
        stat, p = mannwhitneyu(low, high, alternative='two-sided')
        
        print(f"{col}")
        print(f"  U-statistique : {stat:.3f}")
        print(f"  p-value       : {p:.4e}")
